In [18]:
#!/usr/bin/env python
# coding: utf-8

from ax.modelbridge.dispatch_utils import choose_generation_strategy
from ax.modelbridge.generation_strategy import GenerationStep, GenerationStrategy
from ax.utils.notebook.plotting import init_notebook_plotting, render
from ax.modelbridge.modelbridge_utils import get_pending_observation_features
from ax.modelbridge.registry import Models
from ax.service.ax_client import AxClient, ObjectiveProperties
import pandas as pd

def print_trials(trials): 
    for trial in trials:
        print(trial)

def load_from_stats(filename):
    df = pd.read_csv(filename)
    trials = []
    for index, row in df.iterrows():
        if row["trial_status"] == "COMPLETED":
            parameters = {
                "layer1": row["layer1"], 
                "layer2": row["layer2"], 
                "layer3": row["layer3"], 
                "layer4": row["layer4"], 
                "learning_rate": str(row["learning_rate"])
            }
            function = (row["total_accuracy"], 0)
            trials.append((row["trial_index"], parameters, function))
    return trials

if __name__ == '__main__':
    VERBOSE = True

    init_notebook_plotting()

    gen_steps = [
        GenerationStep(
            model=Models.BOTORCH_MODULAR,
            num_trials=-1,
        ),
    ]

    gs = GenerationStrategy(steps=gen_steps)
    
    ax_client = AxClient(enforce_sequential_optimization=True, generation_strategy=gs)
    
    ax_client.create_experiment( 
        name="cifar10",
        parameters=[
            {"name": "layer1", "type": "range", "bounds": [1, 16], "value_type": "int"},
            {"name": "layer2", "type": "range", "bounds": [1, 16], "value_type": "int"},
            {"name": "layer3", "type": "range", "bounds": [1, 16], "value_type": "int"},
            {"name": "layer4", "type": "range", "bounds": [1, 16], "value_type": "int"},
            {"name": "learning_rate", "type": "choice", "value_type": "str", "values": ["0.01", "0.001", "0.0001"], "is_ordered": True},
        ],
        objectives={"total_accuracy": ObjectiveProperties(minimize=False)},
    )
    
    ax_client.save_to_json_file("./cifar10.json")
    ax_client.load_from_json_file("./cifar10.json")

    evaluated_trials = load_from_stats("./stats.csv")

    best_trial = None
    trials = []

    for trial in evaluated_trials:
        print(trial)
        parameters, trial_index = ax_client.attach_trial(parameters=trial[1])
        evaluation = {'total_accuracy': trial[2]}

        if best_trial is None or evaluation["total_accuracy"][0] > best_trial[2]["total_accuracy"][0]:
            best_trial = (trial[0], parameters, evaluation)

        trials.append((trial[0], parameters, evaluation))
        ax_client.complete_trial(trial_index=trial_index, raw_data=evaluation)

    ax_client.get_trials_data_frame().to_csv("./stats.csv")

    if VERBOSE:
        print("VERBOSE MODE: ")
        best_parameters, values = ax_client.get_best_parameters()
        print("best_parameters:", best_parameters)
        print("function at best parameters:", values)
        print("best_trial:", best_trial)

        means, covariances = values
        print("means:", means)
        print("covariances:", covariances)

a, b = ax_client.get_next_trial()



[INFO 07-23 22:19:21] ax.utils.notebook.plotting: Injecting Plotly library into cell. Do not overwrite or delete cell.
[INFO 07-23 22:19:21] ax.utils.notebook.plotting: Please see
    (https://ax.dev/tutorials/visualizations.html#Fix-for-plots-that-are-not-rendering)
    if visualizations are not rendering.


[INFO 07-23 22:19:21] ax.service.ax_client: Starting optimization with verbose logging. To disable logging, set the `verbose_logging` argument to `False`. Note that float values in the logs are rounded to 6 decimal points.
c:\Program Files\Python311\Lib\site-packages\ax\core\parameter.py:518: UserWarning:

`sort_values` is not specified for `ChoiceParameter` "learning_rate". Defaulting to `False` for parameters of `ParameterType` STRING. To override this behavior (or avoid this warning), specify `sort_values` during `ChoiceParameter` construction.

[INFO 07-23 22:19:21] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='layer1', parameter_type=INT, range=[1, 16]), RangeParameter(name='layer2', parameter_type=INT, range=[1, 16]), RangeParameter(name='layer3', parameter_type=INT, range=[1, 16]), RangeParameter(name='layer4', parameter_type=INT, range=[1, 16]), ChoiceParameter(name='learning_rate', parameter_type=STRING, values=['0.01', '0.0

(0, {'layer1': 1, 'layer2': 1, 'layer3': 2, 'layer4': 2, 'learning_rate': '0.001'}, (73.74, 0))
(1, {'layer1': 10, 'layer2': 8, 'layer3': 5, 'layer4': 13, 'learning_rate': '0.01'}, (64.75, 0))
(2, {'layer1': 7, 'layer2': 6, 'layer3': 8, 'layer4': 6, 'learning_rate': '0.01'}, (64.2, 0))
(3, {'layer1': 16, 'layer2': 4, 'layer3': 11, 'layer4': 5, 'learning_rate': '0.01'}, (63.76, 0))
(4, {'layer1': 7, 'layer2': 1, 'layer3': 2, 'layer4': 8, 'learning_rate': '0.01'}, (63.01, 0))
(5, {'layer1': 13, 'layer2': 13, 'layer3': 7, 'layer4': 12, 'learning_rate': '0.0001'}, (81.43, 0))
(6, {'layer1': 10, 'layer2': 14, 'layer3': 11, 'layer4': 10, 'learning_rate': '0.001'}, (80.0, 0))
(7, {'layer1': 1, 'layer2': 7, 'layer3': 12, 'layer4': 8, 'learning_rate': '0.0001'}, (78.48, 0))
(8, {'layer1': 8, 'layer2': 15, 'layer3': 14, 'layer4': 14, 'learning_rate': '0.001'}, (79.96, 0))
(9, {'layer1': 9, 'layer2': 3, 'layer3': 6, 'layer4': 10, 'learning_rate': '0.001'}, (79.25, 0))
(10, {'layer1': 5, 'layer2':

[INFO 07-23 22:19:21] ax.core.experiment: Attached custom parameterizations [{'layer1': 14, 'layer2': 13, 'layer3': 12, 'layer4': 13, 'learning_rate': '0.0001'}] as trial 38.
[INFO 07-23 22:19:21] ax.service.ax_client: Completed trial 38 with data: {'total_accuracy': (81.86, 0)}.
[INFO 07-23 22:19:21] ax.core.experiment: Attached custom parameterizations [{'layer1': 15, 'layer2': 11, 'layer3': 12, 'layer4': 13, 'learning_rate': '0.0001'}] as trial 39.
[INFO 07-23 22:19:21] ax.service.ax_client: Completed trial 39 with data: {'total_accuracy': (81.77, 0)}.
[INFO 07-23 22:19:21] ax.core.experiment: Attached custom parameterizations [{'layer1': 16, 'layer2': 11, 'layer3': 9, 'layer4': 9, 'learning_rate': '0.0001'}] as trial 40.
[INFO 07-23 22:19:21] ax.service.ax_client: Completed trial 40 with data: {'total_accuracy': (81.46, 0)}.
[INFO 07-23 22:19:21] ax.core.experiment: Attached custom parameterizations [{'layer1': 15, 'layer2': 15, 'layer3': 12, 'layer4': 12, 'learning_rate': '0.0001'

(38, {'layer1': 14, 'layer2': 13, 'layer3': 12, 'layer4': 13, 'learning_rate': '0.0001'}, (81.86, 0))
(39, {'layer1': 15, 'layer2': 11, 'layer3': 12, 'layer4': 13, 'learning_rate': '0.0001'}, (81.77, 0))
(40, {'layer1': 16, 'layer2': 11, 'layer3': 9, 'layer4': 9, 'learning_rate': '0.0001'}, (81.46, 0))
(41, {'layer1': 15, 'layer2': 15, 'layer3': 12, 'layer4': 12, 'learning_rate': '0.0001'}, (81.83, 0))
(42, {'layer1': 14, 'layer2': 10, 'layer3': 14, 'layer4': 12, 'learning_rate': '0.0001'}, (81.56, 0))
(43, {'layer1': 16, 'layer2': 13, 'layer3': 12, 'layer4': 12, 'learning_rate': '0.0001'}, (82.02, 0))
(44, {'layer1': 15, 'layer2': 13, 'layer3': 12, 'layer4': 12, 'learning_rate': '0.0001'}, (81.75, 0))
(45, {'layer1': 16, 'layer2': 14, 'layer3': 14, 'layer4': 13, 'learning_rate': '0.0001'}, (81.76, 0))
(46, {'layer1': 16, 'layer2': 11, 'layer3': 14, 'layer4': 12, 'learning_rate': '0.0001'}, (82.21, 0))
(47, {'layer1': 13, 'layer2': 14, 'layer3': 10, 'layer4': 13, 'learning_rate': '0.00

[INFO 07-23 22:19:23] ax.service.ax_client: Generated new trial 50 with parameters {'layer1': 16, 'layer2': 11, 'layer3': 12, 'layer4': 12, 'learning_rate': '0.0001'}.


<h1>PLOTTING

In [23]:

render(ax_client.get_contour_plot(param_x="layer1", param_y="layer2", metric_name="total_accuracy"))
render(ax_client.get_contour_plot(param_x="layer1", param_y="layer3", metric_name="total_accuracy"))
render(ax_client.get_contour_plot(param_x="layer1", param_y="layer4", metric_name="total_accuracy"))
render(ax_client.get_contour_plot(param_x="layer2", param_y="layer3", metric_name="total_accuracy"))
render(ax_client.get_contour_plot(param_x="layer2", param_y="layer4", metric_name="total_accuracy"))
render(ax_client.get_contour_plot(param_x="layer3", param_y="layer4", metric_name="total_accuracy"))
render(ax_client.get_contour_plot(param_x="layer1", param_y="learning_rate", metric_name="total_accuracy"))
render(ax_client.get_contour_plot(param_x="layer2", param_y="learning_rate", metric_name="total_accuracy"))
render(ax_client.get_contour_plot(param_x="layer3", param_y="learning_rate", metric_name="total_accuracy"))
render(ax_client.get_contour_plot(param_x="layer4", param_y="learning_rate", metric_name="total_accuracy"))


[INFO 07-23 22:23:57] ax.service.ax_client: Retrieving contour plot with parameter 'layer1' on X-axis and 'layer2' on Y-axis, for metric 'total_accuracy'. Remaining parameters are affixed to the middle of their range.


[INFO 07-23 22:23:58] ax.service.ax_client: Retrieving contour plot with parameter 'layer1' on X-axis and 'layer3' on Y-axis, for metric 'total_accuracy'. Remaining parameters are affixed to the middle of their range.


[INFO 07-23 22:23:58] ax.service.ax_client: Retrieving contour plot with parameter 'layer1' on X-axis and 'layer4' on Y-axis, for metric 'total_accuracy'. Remaining parameters are affixed to the middle of their range.


[INFO 07-23 22:23:58] ax.service.ax_client: Retrieving contour plot with parameter 'layer2' on X-axis and 'layer3' on Y-axis, for metric 'total_accuracy'. Remaining parameters are affixed to the middle of their range.


[INFO 07-23 22:23:59] ax.service.ax_client: Retrieving contour plot with parameter 'layer2' on X-axis and 'layer4' on Y-axis, for metric 'total_accuracy'. Remaining parameters are affixed to the middle of their range.


[INFO 07-23 22:23:59] ax.service.ax_client: Retrieving contour plot with parameter 'layer3' on X-axis and 'layer4' on Y-axis, for metric 'total_accuracy'. Remaining parameters are affixed to the middle of their range.


[INFO 07-23 22:23:59] ax.service.ax_client: Retrieving contour plot with parameter 'layer1' on X-axis and 'learning_rate' on Y-axis, for metric 'total_accuracy'. Remaining parameters are affixed to the middle of their range.


ValueError: learning_rate is not a RangeParameter

In [ ]:
render(
    ax_client.get_optimization_trace()
)  